In [1]:

import pandas as pd
df=pd.read_csv("globalterrorismdb_0718dist.csv",engine = 'python',encoding = 'ISO-8859-1')

In [2]:
import numpy as np
df.country.isnull().sum()

0

In [3]:
df.columns
sampled_df = df.groupby((df['iyear']), group_keys=False).apply(lambda x: x.sample(n=min(len(x), 500)))

In [4]:
sampled_df.dropna(subset='longitude',inplace=True)
sampled_df.dropna(subset='latitude',inplace=True)
sampled_df.dropna(subset='country_txt',inplace=True)
sampled_df.dropna(subset='city',inplace=True)

In [5]:
df.columns

Index(['eventid', 'iyear', 'imonth', 'iday', 'approxdate', 'extended',
       'resolution', 'country', 'country_txt', 'region',
       ...
       'addnotes', 'scite1', 'scite2', 'scite3', 'dbsource', 'INT_LOG',
       'INT_IDEO', 'INT_MISC', 'INT_ANY', 'related'],
      dtype='object', length=135)

In [14]:
df_new=pd.DataFrame()
df_new['country']=sampled_df.country_txt
df_new['latitude']=sampled_df.latitude
df_new['longitude']=sampled_df.longitude
df_new['year']=sampled_df.iyear
df_new['targ_type']=sampled_df.targtype1_txt

df_new['wep_typ']=sampled_df.weaptype1_txt
df_new['region']=sampled_df.region_txt
df_new['city']=sampled_df.city
df_new['attack_type'] = sampled_df.attacktype1_txt
#df_new['gang_name']=sampled_df.gname

In [7]:
cf_new=df_new.copy()
cf_new.city.unique()

array(['Lawrence', 'San Francisco', 'London', ..., 'Tarwadeeh', 'Milhah',
       'Umuahia'], dtype=object)

In [8]:
cf_new.isnull().sum()

country      0
latitude     0
longitude    0
year         0
targ_type    0
wep_typ      0
region       0
city         0
dtype: int64

In [9]:
drop_list=cf_new.city.unique().tolist()
drop_list.sort()

In [10]:
drop_list.insert(0,None)

In [11]:
labels = drop_list[1:]
labels.insert(0,"ALL")

In [16]:
targ_list = cf_new.targ_type.unique().tolist()
targ_list.insert(0,None)
Tlabels = targ_list[1:]
Tlabels.insert(0,"ALL")
x_axis_ticks = cf_new['year'].unique().tolist()
x_ticks = x_axis_ticks[::5]
x_ticks

[1970, 1975, 1980, 1985, 1990, 1996, 2001, 2006, 2011, 2016]

In [21]:
import altair as alt
import pandas as pd
import altair as alt
alt.data_transformers.disable_max_rows()
interval = alt.selection_single(fields=['longitude','latitude'])

url = "https://raw.githubusercontent.com/deldersveld/topojson/master/world-continents.json"
source = alt.topo_feature(url, "continent")

selection2 = alt.selection_multi(fields=['wep_typ'], bind='legend')
selection3 = alt.selection_multi(fields=['region'], bind='legend')

input_dropdown = alt.binding_select(options=drop_list, name='Cities',labels=labels)
selection_country = alt.selection_single(fields=['city'], bind=input_dropdown)

targ_dropdown = alt.binding_select(options=targ_list, name='Target Types',labels=Tlabels)
sel_target = alt.selection_single(fields=['targ_type'], bind=targ_dropdown)

base = alt.Chart(source).mark_geoshape(
    fill='lightgray',
    stroke='white'
).project('mercator').properties(
    width=400,
    height=300
)



country_selection = alt.selection_multi(fields=['country'])
brush = alt.selection(type="interval")
brush2 = alt.selection_single(fields=['country'])
general = alt.selection_single(fields=['wep_typ'])
#general1 = alt.selection_single(fields=['country','wep_typ'])


#brush = alt.selection_single(fields=['year'],type='interval')


points = alt.Chart(df_new).mark_point().encode(
    longitude='longitude:Q',
    latitude='latitude:Q',
    tooltip=['country:N','year:N','wep_typ:N','year:Q'],
    color=alt.condition(
        (brush&selection3&brush2 ), 'wep_typ:N', alt.value('darkgrey')),
    size=alt.condition(
        selection2, alt.value(1), alt.value(0)
    ),
shape=alt.Shape('region:N',legend = alt.Legend(title = 'Regions',orient = 'left'))).add_selection(brush2).add_selection(selection2).add_selection(selection3).add_selection(selection_country).add_selection(brush2
).add_selection(sel_target).transform_filter(selection_country).transform_filter(sel_target)



bar1 = alt.Chart(df_new).mark_bar().encode(
    x='year',
    y=alt.Y('count()'),
    color=alt.condition(brush2, 'wep_typ:N', alt.value('darkgrey'),
                       legend = alt.Legend(title = 'Weapon Type',orient = 'right')),
    tooltip=['country:N','wep_typ:N','year:Q']
).properties(
    width=200,
    height=300
).add_selection(brush).add_selection(selection_country).transform_filter(selection_country).add_selection(sel_target).transform_filter(sel_target)

#x=base+points
x = base + points
sd=x.properties(title='Global Terrorist Attacks (1970-2017)') | bar1.properties(title=' Yearly Global Terrorist Attacks by Weapon Type')



#(points).properties(title='Global Terrorist Attacks').configure_title(fontSize=20)

sd.save("viz1final.html")
sd

alt.HConcatChart(...)